In [1]:
import sys
import pickle
# import cPickle
from datetime import datetime, timezone, timedelta
from enum import Enum
import numpy as np
import pandas as pd

from pathlib import Path
import matplotlib.colors as mcolors

# from PyQt5 import QtGui, QtWidgets
# from PyQt5.QtWidgets import QMessageBox, QToolTip, QStackedWidget, QHBoxLayout, QVBoxLayout, QSplitter, QFormLayout, QLabel, QFrame, QPushButton, QTableWidget, QTableWidgetItem, QScrollArea
# from PyQt5.QtWidgets import QApplication, QFileSystemModel, QTreeView, QWidget, QAction, qApp, QApplication, QTreeWidgetItem, QFileDialog 
# from PyQt5.QtGui import QPainter, QBrush, QPen, QColor, QFont, QIcon
# from PyQt5.QtCore import Qt, QPoint, QRect, QObject, QEvent, pyqtSignal, pyqtSlot, QSize, QDir, QThreadPool

# from GUI.UI.AbstractDatabaseAccessingWidgets import AbstractDatabaseAccessingQObject

from app.filesystem.VideoUtils import findVideoFiles, VideoParsedResults, FoundVideoFileResult, CachedFileSource
# from app.filesystem.Workers.VideoMetadataWorkers import VideoMetadataWorker, VideoMetadataWorkerSignals
# from app.filesystem.Workers.VideoFilesystemWorkers import VideoFilesystemWorker, VideoFilesystemWorkerSignals
from app.filesystem.Workers.VideoMetadataWorkers import VideoMetadataWorker
from app.filesystem.Workers.VideoFilesystemWorkers import VideoFilesystemWorker

from GUI.Model.ModelViewContainer import ModelViewContainer
from app.filesystem.FilesystemOperations import OperationTypes, PendingFilesystemOperation
from app.filesystem.LabjackEventsLoader import LabjackEventsLoader, PhoServerFormatArgs

from app.filesystem.FilesystemRecordBase import FilesystemRecordBase, FilesystemLabjackEvent_Record
from GUI.Model.Events.PhoDurationEvent import PhoDurationEvent

from app.filesystem.LabjackFilesystemLoadingMixin import LabjackEventFile, LabjackFilesystemLoader

In [ ]:
## Event Loading:

## User-configurable settings:
# should_filter_for_invalid_events = True
should_filter_for_invalid_events = False
aFoundLabjackDataFile = Path("I:/EventData/BB01/out_file_s470017560_20190911-20190820_46Combined.csv")
videoStartDates = []
videoEndDates = []

active_cache = dict()
# LabjackEventFile: this serves as a container to hold the loaded events
outEventFileObj = LabjackEventFile(aFoundLabjackDataFile)

(dateTimes, labjackEventContainers, phoServerFormatArgs) = LabjackFilesystemLoader.loadLabjackEventsFile(aFoundLabjackDataFile, videoStartDates, videoEndDates, shouldLimitEventsToVideoDates=False, usePhoServerFormat=True, phoServerFormatIsStdOut=False, should_filter_for_invalid_events=should_filter_for_invalid_events)

print('Loading complete... setting loaded values')
# Cache the loaded values into the LabjackEventFile object.
# outEventFileObj.set_loaded_values(dateTimes, [], [], labjackEventContainers, phoServerFormatArgs)
outEventFileObj.set_loaded_values(dateTimes, [], [], labjackEventContainers, None)
print('done updating cache...')

if (not (aFoundLabjackDataFile in active_cache.keys())):
    # print('Creating new cache entry for {}...'.format(str(aFoundLabjackDataFile)))
    # Parent doesn't yet exist in cache
    active_cache[aFoundLabjackDataFile] = outEventFileObj
else:
    # Parent already exists
    print("WARNING: labjack file path {} already exists in the temporary cache. Updating its values...".format(str(aFoundLabjackDataFile)))
    active_cache[aFoundLabjackDataFile] = outEventFileObj
    pass

            

In [2]:
""" Import Dataframe to file:
"""
# dataframe_import_path = 'data/output/LabjackDataExport/output_dataframe_1-9-2020'
out_dataframe_export_parent_path = Path('data/output/LabjackDataExport/')
out_dataframe_export_path_basic = out_dataframe_export_parent_path.joinpath('output_dataframe_1-9-2020_basic_store.h5') # Used for basic objects
out_dataframe_export_path_pandas = out_dataframe_export_parent_path.joinpath('output_dataframe_1-9-2020_pandas_store.h5') # Used for pandas Dataframe and Series objects
        
# # Basic
# active_path = out_dataframe_export_path_basic
# print('Reading data from file {}...'.format(str(active_path)))
# active_store = pd.HDFStore(active_path)
# print(active_store)
# # in_df = active_store['variables_dataframe']
# active_store.close()
# print('done reading {}.'.format(str(active_path)))

# Pandas:
active_path = out_dataframe_export_path_pandas
print('Reading data from file {}...'.format(str(active_path)))
active_store = pd.HDFStore(active_path)
print(active_store)
in_df = active_store['variables_dataframe']
in_series = active_store['variables_series_of_dataframes']
active_store.close()
print('done reading {}.'.format(str(active_path)))


# in_df
# for (aVariableIndex, aVariableData) in enumerate(variableData):
#     aVariableData['']
        
#         print('Converting variableData to Pandas Dataframe...')
#         out_df = get_variables_as_dataframe(variableData, active_labjack_variable_names)
#         # out_df.to_json(orient='split')

Reading data from file data\output\LabjackDataExport\output_dataframe_1-9-2020_pandas_store.h5...
<class 'pandas.io.pytables.HDFStore'>
File path: data\output\LabjackDataExport\output_dataframe_1-9-2020_pandas_store.h5

__setstate__(state: {'start_date': datetime.datetime(2019, 9, 16, 21, 0, 7, 491000), 'end_date': None, 'variable_name': 'Water1_BeamBreak', 'variable_color': <PyQt5.QtGui.QColor object at 0x00000232F87F8CF8>, 'extended_info_dict': {'videoIndex': 26, 'video_relative_offset': datetime.timedelta(0, 11198, 458000), 'event_type': 'BeamBreak', 'dispense_type': 'BeamBreak', 'port': 'Water1'}})
__setstate__(state: {'start_date': datetime.datetime(2019, 9, 16, 21, 0, 7, 796000), 'end_date': None, 'variable_name': 'Water1_BeamBreak', 'variable_color': <PyQt5.QtGui.QColor object at 0x00000232F87F8CF8>, 'extended_info_dict': {'videoIndex': 26, 'video_relative_offset': datetime.timedelta(0, 11198, 763000), 'event_type': 'BeamBreak', 'dispense_type': 'BeamBreak', 'port': 'Water1'}})


IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)




__setstate__(state: {'start_date': datetime.datetime(2019, 8, 20, 4, 18, 34, 93000), 'end_date': None, 'variable_name': 'Water2_BeamBreak', 'variable_color': <PyQt5.QtGui.QColor object at 0x00000232F868E908>, 'extended_info_dict': {'videoIndex': 206, 'video_relative_offset': datetime.timedelta(0, 6248, 41000), 'event_type': 'BeamBreak', 'dispense_type': 'BeamBreak', 'port': 'Water2'}})
__setstate__(state: {'start_date': datetime.datetime(2019, 8, 20, 4, 18, 34, 597000), 'end_date': None, 'variable_name': 'Water2_BeamBreak', 'variable_color': <PyQt5.QtGui.QColor object at 0x00000232F868E908>, 'extended_info_dict': {'videoIndex': 206, 'video_relative_offset': datetime.timedelta(0, 6248, 545000), 'event_type': 'BeamBreak', 'dispense_type': 'BeamBreak', 'port': 'Water2'}})
__setstate__(state: {'start_date': datetime.datetime(2019, 8, 20, 4, 18, 35, 152000), 'end_date': None, 'variable_name': 'Water2_BeamBreak', 'variable_color': <PyQt5.QtGui.QColor object at 0x00000232F868E908>, 'extended

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [3]:
in_series

Water1_BeamBreak                      timestamps  values videoIndi...
Water2_BeamBreak                      timestamps  values videoIndi...
Food1_BeamBreak                       timestamps  values videoIndi...
Food2_BeamBreak                        timestamps  values videoInd...
Water1_Dispense                      timestamps  values videoIndic...
Water2_Dispense                       timestamps  values videoIndi...
Food1_Dispense                       timestamps  values videoIndic...
Food2_Dispense                         timestamps  values videoInd...
dtype: object

In [4]:
in_series.shape

(8,)

In [5]:
in_series.index

Index(['Water1_BeamBreak', 'Water2_BeamBreak', 'Food1_BeamBreak',
       'Food2_BeamBreak', 'Water1_Dispense', 'Water2_Dispense',
       'Food1_Dispense', 'Food2_Dispense'],
      dtype='object')

In [12]:
str(in_series.Water1_BeamBreak.variableSpecificRecords)

'0       <app.filesystem.FilesystemRecordBase.Filesyste...\n1       <app.filesystem.FilesystemRecordBase.Filesyste...\n2       <app.filesystem.FilesystemRecordBase.Filesyste...\n3       <app.filesystem.FilesystemRecordBase.Filesyste...\n4       <app.filesystem.FilesystemRecordBase.Filesyste...\n                              ...                        \n1428    <app.filesystem.FilesystemRecordBase.Filesyste...\n1429    <app.filesystem.FilesystemRecordBase.Filesyste...\n1430    <app.filesystem.FilesystemRecordBase.Filesyste...\n1431    <app.filesystem.FilesystemRecordBase.Filesyste...\n1432    <app.filesystem.FilesystemRecordBase.Filesyste...\nName: variableSpecificRecords, Length: 1433, dtype: object'

In [ ]:
in_df = in_df.T

In [ ]:
in_df.shape

In [ ]:
in_df.index

In [ ]:
in_df.columns

In [ ]:
in_df.dtypes

In [ ]:
in_df.variableSpecificRecords

In [ ]:
# in_df.axes
in_df.head(20)